# Dataloading 01

In this notebook, we'll figure out how to use PyTorch's DataLoader class to load our massive files without reading the entirety of them into memory

In [75]:
import comet_ml
import dask.dataframe as dd
import pandas as pd 
import torch
import linecache 
import csv
import numpy as np
import torch.nn as nn
from torch.utils.data import Dataset, DataLoader
import pytorch_lightning as pl
import torch.nn.functional as F
import sys, os
from pathlib import Path
from sklearn.utils.class_weight import compute_class_weight

here = Path().cwd()

We'll first design a custom dataset to use with PyTorch's `DataLoader` class

In [100]:
class GeneExpressionData(Dataset):
    def __init__(self, filename, labelname):
        self._filename = filename
        self._labelname = pd.read_csv(labelname)
        self._total_data = 0
        
        with open(filename, "r") as f:
            self._total_data = len(f.readlines()) - 1
    
    def __getitem__(self, idx):
        line = linecache.getline(self._filename, idx + 2)
        csv_data = csv.reader([line])
        data = [x for x in csv_data][0]
        
        label = self._labelname.loc[idx, '# label']
        return torch.from_numpy(np.array([float(x) for x in data])).float(), label
    
    def __len__(self):
        return self._total_data
    
    def num_labels(self):
        return self._labelname['# label'].nunique()
    
    def num_features(self):
        return len(self.__getitem__(0)[0])

    def compute_class_weights(self):
        weights = compute_class_weight(
            class_weight='balanced', 
            classes=np.unique(self._labelname['# label'].values), 
            y=self._labelname['# label'].values
        )    

        weights = torch.from_numpy(weights)
        return weights.float().to('cuda')

Since PyTorch loss functions require classes in $[0, C]$, we'll first add $1$ to the labels and re-write it out so we can use it for training

In [101]:
def fix_labels(file):
    labels = pd.read_csv(file)
    labels['# label'] = labels['# label'].astype(int) + 1
    labels.to_csv('fixed_' + file.split('/')[-1], index=False)

fix_labels('../data/processed/meta_primary_labels.csv')

Great, we now continue as normal

In [102]:
t = GeneExpressionData(
    filename=os.path.join(here, '../data/processed/umap/primary_reduction_neighbors_100_components_3.csv'),
    labelname=os.path.join('../data/processed/meta_primary_labels.csv')
)
t.compute_class_weights()

[ 0  1  2  3  4  5  6  7  8  9 10 11 12 13 14 15 16 17 18 19 20 21 22 23
 24 25 26 27 28 29]


tensor([ 23.5583,   1.7000,  23.2975,   4.5162,   4.2203,   6.5156,   0.6397,
          1.6949,   0.6687,   0.8051,   0.3609,   6.2326,   4.8905,   1.9614,
         17.3929,   0.1903,   3.3441,   2.1526,   1.8785,   0.7911,   0.3222,
          0.7065,   0.4820,   0.9035,   1.5354,   3.3459,   0.7220,   2.0976,
        170.6387,   0.5595], dtype=torch.float64)

Let's see how fast it takes to load a minibatch of data

In [68]:
%%time 

for i in range(0,100):
    print(t.__getitem__(i))

(tensor([6.3848, 2.4303, 7.7812]), 26)
(tensor([6.3639, 2.4563, 7.7301]), 26)
(tensor([6.3428, 2.4779, 7.7295]), 8)
(tensor([6.3877, 2.4754, 7.7310]), 15)
(tensor([6.4995, 2.5715, 7.8413]), 8)
(tensor([6.4212, 2.4951, 7.7277]), 8)
(tensor([6.3750, 2.5142, 7.6449]), 29)
(tensor([6.3622, 2.5209, 7.6304]), 8)
(tensor([6.3773, 2.5858, 7.6911]), 8)
(tensor([6.4225, 2.5520, 7.7651]), 15)
(tensor([6.3794, 2.5182, 7.7005]), 29)
(tensor([6.4494, 2.6395, 7.6515]), 8)
(tensor([6.2893, 2.7212, 7.7196]), 8)
(tensor([6.4438, 2.6235, 7.7850]), 15)
(tensor([6.3955, 2.4870, 7.7330]), 8)
(tensor([6.4113, 2.5882, 7.7068]), 29)
(tensor([6.3515, 2.5249, 7.6835]), 24)
(tensor([2.5176, 5.6257, 3.4814]), 14)
(tensor([6.4297, 2.5550, 7.7791]), 8)
(tensor([6.3944, 2.6301, 7.7066]), 8)
(tensor([6.3972, 2.5236, 7.7470]), 6)
(tensor([6.4212, 2.5425, 7.7602]), 8)
(tensor([6.4844, 2.5889, 7.7253]), 8)
(tensor([6.4816, 2.5496, 7.7555]), 16)
(tensor([6.3856, 2.6333, 7.7570]), 6)
(tensor([6.3817, 2.5582, 7.7225]), 8)
(

Before we train our model, we need to split our data into training and testing sets, in order to get an unbiased evaluation of our model's performance. Likely, we will initially overfit the training set since we provide no regularization.

In [14]:
train_size = int(0.8 * len(t))
test_size = len(t) - train_size

train, test = torch.utils.data.random_split(t, [train_size, test_size])

In [15]:
traindata = DataLoader(train, batch_size = 8, num_workers = 0)
valdata = DataLoader(test, batch_size = 8, num_workers = 0)

In [17]:
for X, y in traindata:
    print(X, y)

tensor([[ 3.4116,  4.3611,  3.6923],
        [ 1.9499,  3.7356,  6.1307],
        [ 1.0966,  0.4327,  5.5884],
        [ 2.6846,  7.8154,  6.6181],
        [ 4.5364,  6.9276,  2.7043],
        [ 0.7097, -0.3879,  5.3842],
        [ 1.8299,  2.5179,  1.5972],
        [ 2.5743,  7.7902,  6.7043]]) tensor([15, 12,  4,  9, 13,  4, 15,  9])
tensor([[ 4.2022,  8.7407,  1.4905],
        [ 6.6213,  7.5119,  0.7633],
        [ 2.6400,  8.4390,  6.2129],
        [-1.3735,  8.4140,  2.3972],
        [ 4.1918,  4.3778,  3.5796],
        [ 2.8546,  8.0918,  6.0737],
        [-2.7102,  3.1529,  5.9547],
        [-2.3790,  3.5089,  6.2377]]) tensor([ 8,  8,  9, 11, 15,  0,  3,  3])
tensor([[ 2.3997,  7.2758,  3.2588],
        [ 1.4293,  5.1844,  3.4736],
        [ 2.0637,  1.4185,  2.8869],
        [ 5.0089,  5.8322, -0.9349],
        [ 5.1753,  4.2075,  5.1987],
        [ 2.3370,  9.0350,  2.4659],
        [ 1.9502,  3.6692,  6.2672],
        [ 1.3264,  9.7038,  5.3532]]) tensor([10,  0, 15,  8, 12,

tensor([[-2.7478,  3.6829,  5.8313],
        [-2.5611,  3.0203,  6.4444],
        [ 4.9854,  5.8952,  4.5249],
        [-2.5121,  3.1054,  6.2594],
        [-2.5242,  3.4251,  5.8270],
        [ 2.1844,  1.2057,  2.7340],
        [ 1.4234,  8.3443, -0.7206],
        [-0.6267,  3.9891,  4.3014]]) tensor([ 3,  3,  8,  3,  3, 15,  9,  0])
tensor([[-0.8864,  1.6219,  5.7295],
        [ 2.6921,  3.7845,  6.5563],
        [ 3.5187,  7.6315,  3.3477],
        [ 2.3783,  9.0114,  2.2746],
        [-1.5731,  8.5866,  2.4652],
        [ 2.3053,  7.3353,  3.3078],
        [ 4.0524,  4.4479,  4.7053],
        [ 3.2431,  5.2917,  3.7889]]) tensor([ 4, 12, 14,  9, 11, 10, 12,  0])
tensor([[ 1.5196,  1.8262,  2.9626],
        [ 6.8126,  7.8132,  3.8017],
        [-2.9219,  4.6821,  5.3783],
        [ 4.1805,  8.8457,  1.4872],
        [-1.9178,  8.1225,  3.3194],
        [ 2.7356,  0.4884,  2.2067],
        [ 3.3459,  2.6750,  4.5240],
        [ 1.2887,  1.3725,  1.8575]]) tensor([15,  8,  3,  8,  0,

        [ 3.4790,  6.5520,  4.8415]]) tensor([ 4, 15, 11, 15, 10,  8,  8,  9])
tensor([[ 3.8245,  5.6319,  2.7255],
        [ 2.0514, 11.3805,  5.8315],
        [ 3.4684,  6.5693,  3.4868],
        [ 3.0782,  7.6227,  4.9318],
        [ 2.5396,  7.4892,  4.4655],
        [ 2.5059,  7.3475,  3.4376],
        [-4.0559,  4.9390,  1.6056],
        [ 0.2598,  4.6911,  4.8763]]) tensor([ 8,  9, 14,  8,  8, 10, 11, 12])
tensor([[ 4.0558,  2.3200,  4.8797],
        [ 3.7718,  6.9656,  3.7377],
        [-0.1403,  0.1820,  5.1755],
        [ 2.4506,  4.3804,  2.7011],
        [-0.3305,  8.3629,  4.8598],
        [ 2.1617,  2.5490,  1.5321],
        [ 3.9690,  4.0832,  3.1315],
        [ 3.8429,  4.2248,  5.1621]]) tensor([15, 14,  4,  0, 11, 15, 15, 12])
tensor([[ 6.5845,  7.5000,  3.7077],
        [ 3.8364,  6.8131,  3.3949],
        [ 0.9454,  0.2969,  7.2429],
        [ 2.8971,  4.1229,  2.1365],
        [ 2.7127,  8.4239,  6.2937],
        [ 0.5244,  3.3007,  5.3820],
        [ 1.2955,  1.54

        [ 3.5958,  1.5807,  2.6426]]) tensor([14, 15, 12,  0, 12, 14,  8, 15])
tensor([[ 0.7062,  3.6128,  5.3429],
        [ 0.8739, 11.5135,  6.0867],
        [ 0.8082,  3.7082,  6.4030],
        [-4.2530,  4.9736,  1.8340],
        [ 7.3218,  7.7414,  0.3060],
        [ 6.0422,  7.1128,  3.0705],
        [ 3.2799,  4.4006,  3.6468],
        [ 0.7650,  8.7596,  2.4584]]) tensor([12,  9, 12, 11,  8,  8, 15, 11])
tensor([[-1.9051,  8.1231,  3.3113],
        [ 0.0092,  4.5269,  4.7555],
        [ 3.0771,  4.5031,  3.5876],
        [ 1.1553, -0.3164,  6.8872],
        [ 7.2752,  0.8497,  7.3419],
        [ 3.6179,  2.6029,  5.0710],
        [-1.9818,  7.3484,  3.6077],
        [ 3.3180,  7.2062,  3.6986]]) tensor([11, 12, 15,  4,  1, 15, 11, 10])
tensor([[ 2.9067,  5.3198,  3.5641],
        [-2.9942,  4.9738,  2.2761],
        [ 2.3580,  8.9273,  2.2548],
        [-2.4545,  3.6642,  5.9809],
        [-2.9185,  4.9526,  1.9117],
        [ 3.4120,  1.9437,  2.8388],
        [ 2.7111,  8.37

        [ 3.8167,  7.4656,  2.6617]]) tensor([15, 11,  0, 10,  0, 15,  4, 14])
tensor([[8.0244, 0.0247, 6.6550],
        [4.2083, 7.5611, 2.7179],
        [3.1999, 7.2354, 3.2173],
        [1.1601, 8.9575, 1.5272],
        [2.5677, 0.0127, 6.3376],
        [2.4828, 6.8963, 3.6811],
        [1.0582, 7.4730, 0.7487],
        [3.2882, 2.0437, 2.8710]]) tensor([ 1, 14, 14,  9,  4,  9, 10, 15])
tensor([[ 2.8305,  3.4995,  6.3617],
        [ 1.6596,  3.0123,  6.9386],
        [ 3.2547,  2.8233,  4.6956],
        [ 2.8577,  3.0561,  1.2230],
        [ 1.2129,  4.5423,  5.3098],
        [ 2.3234,  9.1082,  2.5931],
        [ 1.9967,  7.8820,  2.9852],
        [-3.3201,  5.3073,  6.0503]]) tensor([12, 12, 15, 15,  0,  9, 10, 11])
tensor([[ 4.4417,  2.4624,  4.7021],
        [ 3.2335,  1.2618,  3.7689],
        [ 0.1633,  4.5981,  4.8420],
        [-3.2934,  4.9876,  1.5665],
        [ 3.5828,  1.1932,  2.3301],
        [ 2.9990,  6.4920,  4.2890],
        [ 3.2390,  8.0341,  6.9725],
        [ 

...

tensor([[-0.7753,  9.0522,  3.7319],
        [-0.2993,  1.0095,  6.5668],
        [-3.4309,  7.2440,  3.7791],
        [ 4.8595,  3.0695,  4.2853],
        [ 4.5794,  9.0477,  3.8832],
        [ 0.9203,  3.7185,  6.6308],
        [ 1.0715,  7.8302,  2.4011],
        [-1.7194,  8.6774,  2.5449]]) tensor([11,  4, 11, 12,  8, 12, 11, 11])
tensor([[ 2.4486,  3.6057,  1.1274],
        [ 0.1088,  4.5438,  4.8784],
        [ 4.9139,  2.8374,  4.2969],
        [-3.6582,  5.1556,  6.2920],
        [-1.6466,  8.6313,  2.5602],
        [ 5.0933,  4.1558,  5.4571],
        [ 1.9689,  4.0900,  5.5763],
        [-0.0360,  4.0454,  4.7404]]) tensor([15, 12, 12, 11, 11,  0, 12, 12])
tensor([[ 1.4681,  3.5624,  6.9563],
        [ 0.8352, 11.5274,  5.9853],
        [ 1.5603,  2.7729,  6.3631],
        [ 2.3113,  8.4643,  2.0605],
        [-2.9555,  4.8984,  2.2113],
        [-1.6517,  8.0099,  3.3333],
        [ 0.3540,  9.2726,  4.0357],
        [ 1.4074,  8.0686, -0.6747]]) tensor([12,  9, 12,  9, 11,

        [ 3.5289,  6.7647,  2.7798]]) tensor([14, 12,  8,  8,  4,  1,  8, 14])
tensor([[ 1.1974,  1.8583,  1.5243],
        [-1.0739,  1.5283,  5.9988],
        [ 2.7347,  2.0905,  3.6399],
        [ 4.4195,  4.2221,  5.8639],
        [ 3.3739,  7.0799,  6.6716],
        [ 1.6930,  3.2483,  6.9683],
        [ 1.3309,  1.6274,  1.5002],
        [-2.8597,  3.5316,  5.9285]]) tensor([15,  4, 15, 12,  9, 12, 15,  0])
tensor([[ 0.7901,  3.9810,  5.8631],
        [ 2.7750,  2.0416,  3.8244],
        [ 2.3836,  0.3135,  6.6771],
        [ 3.6674,  7.4889,  3.2138],
        [ 2.6755,  2.8045,  1.3333],
        [ 7.1224,  0.5922,  7.4050],
        [ 0.0307,  3.3968,  6.2175],
        [-2.6019,  2.9728,  6.4060]]) tensor([12,  0,  4, 14, 15,  1, 12,  3])
tensor([[ 1.5925,  2.6158,  1.8610],
        [ 6.5297,  6.6517, -0.2940],
        [ 7.0952,  5.3123,  0.1688],
        [ 8.2116,  0.5887,  7.0483],
        [-0.1592,  4.0009,  6.3633],
        [-3.4564,  7.3296,  2.7495],
        [ 7.9412,  0.82

tensor([[-2.6168,  3.5495,  5.7414],
        [-0.2867,  4.6106,  4.5287],
        [ 2.5358,  7.4762,  4.4212],
        [ 2.5060,  8.7310,  5.3637],
        [ 4.2818,  7.5413,  2.7098],
        [ 3.5503,  6.9557,  2.6696],
        [-2.6052,  2.8215,  6.2527],
        [ 0.4670,  9.2794,  3.3891]]) tensor([ 3, 12,  8,  9, 14, 14,  3, 11])
tensor([[ 1.9243,  7.5080,  3.0408],
        [ 4.0912,  4.2909,  3.5491],
        [ 1.4864,  0.7120,  6.0805],
        [ 8.2116,  6.4040,  1.4544],
        [ 3.9932,  8.7090,  0.6773],
        [ 2.6244, 10.3134,  4.5692],
        [ 1.3619,  3.5828,  6.9508],
        [ 1.4863,  9.4668,  1.9632]]) tensor([10, 15,  4,  8,  8,  9, 12,  9])
tensor([[-2.6571,  3.6654,  5.6486],
        [ 4.2129,  4.2153,  3.3506],
        [ 3.2101,  2.8579,  4.6979],
        [ 4.2888,  4.3640,  4.7375],
        [ 3.3263,  4.4097,  3.6565],
        [ 6.8291,  7.9002,  3.7835],
        [-3.0948,  4.9234,  1.6215],
        [-4.4158,  5.4295,  2.3260]]) tensor([ 0, 15, 15, 12, 15,

tensor([[ 3.6759e+00,  6.6284e+00,  3.4904e+00],
        [ 8.0278e+00,  5.8577e+00,  3.0918e+00],
        [ 6.3356e+00,  7.0573e+00,  4.4382e-01],
        [ 1.6549e+00,  7.3215e-01,  6.2947e+00],
        [-1.0628e+00,  1.4265e+00,  6.3414e+00],
        [-8.5233e-03,  9.1893e+00,  4.9875e+00],
        [ 3.4831e+00,  1.8102e+00,  2.7012e+00],
        [ 3.6547e+00,  7.3409e+00,  3.8670e+00]]) tensor([14,  8,  8,  4,  4, 11,  0,  5])
tensor([[-2.7472e+00,  3.6053e+00,  5.6268e+00],
        [ 1.1979e+00,  5.0089e+00,  5.6727e+00],
        [ 8.6889e-01,  4.4240e+00,  4.9226e+00],
        [ 6.5827e+00,  4.9665e+00,  5.2966e-03],
        [ 2.0969e+00,  8.7125e+00,  3.5446e+00],
        [-1.0332e+00,  1.4741e+00,  6.4913e+00],
        [ 1.2509e+00,  2.6722e+00,  1.8367e+00],
        [-4.1787e+00,  4.9323e+00,  5.6986e+00]]) tensor([ 3, 12,  0,  8,  0,  4, 15, 11])
tensor([[ 2.6934,  1.9817,  4.0767],
        [ 5.5782,  6.4127,  5.0229],
        [ 4.0172,  5.8265,  4.0782],
        [ 3.8923,  4.

tensor([[ 4.9275,  4.1779,  4.7594],
        [ 1.2215, 10.8776,  5.2317],
        [-0.4301,  3.0782,  4.7549],
        [-3.8639,  4.7414,  3.7577],
        [ 3.5576,  7.4430,  3.3960],
        [ 2.6536,  2.0898,  3.6672],
        [ 2.6913,  1.9161,  3.9458],
        [ 3.7659,  4.4785,  5.8390]]) tensor([12,  9, 12, 11, 14, 15, 15, 12])
tensor([[ 2.6183,  8.7051,  5.3909],
        [ 2.3285,  8.4616,  2.0439],
        [ 0.7483,  3.8166,  5.4844],
        [ 3.6109,  1.4836,  2.5665],
        [ 0.5612,  0.4190,  5.9018],
        [ 2.4605, 10.9523,  4.6353],
        [-3.4623,  7.0871,  2.6429],
        [ 1.9833,  1.5453,  2.8775]]) tensor([ 0,  9, 12, 15,  0,  9, 11, 15])
tensor([[ 2.1774,  2.5964,  1.6517],
        [ 0.8174, -0.2100,  5.3450],
        [ 3.6344,  6.5865,  3.4789],
        [ 4.1337,  4.4150,  3.6802],
        [ 2.6018,  8.8763,  5.1789],
        [-0.9860,  1.5335,  6.5730],
        [ 3.1408,  5.6672,  2.7354],
        [ 3.1053,  6.5298,  4.4137]]) tensor([15,  4, 14, 15,  9,

For clarity, let's define a data generation method that simply returns the train and test split from our gene expression dataset

In [16]:
def data_gen():
    t = GeneExpressionData(
        filename=os.path.join(here, '../data/processed/umap/primary_reduction_neighbors_100_components_3.csv'),
        labelname=os.path.join(here, 'fixed_primary_labels_neighbors_50_components_50_clust_size_100.csv')
    )

    train_size = int(0.8 * len(t))
    test_size = len(t) - train_size

    train, test = torch.utils.data.random_split(t, [train_size, test_size])
    
    return train, test

Now that we've defined our `DataLoader`, let's test it when training a simple Neural Network

## Using PyTorch Lightning

PyTorch lightning seems nicer than Ignite, especially for GPU training. Let's test it out 

In [17]:
from torchmetrics import Accuracy, ConfusionMatrix
from sklearn.utils.class_weight import compute_class_weight

class GeneClassifier(pl.LightningModule):
    def __init__(self, N_features, N_labels, weights, config):
        """
        Initialize the gene classifier neural network

        Parameters:
        N_features: Number of features in the inpute matrix 
        N_labels: Number of classes 
        """
        
        self.train_data, self.test_data = data_gen()
        
        # Params for optimizer 
        self.lr = config['lr']
        self.momentum = config['momentum']
        self.weight_decay = config['weight_decay']
        
        super(GeneClassifier, self).__init__()
        self.flatten = nn.Flatten()
        self.linear_relu_stack = nn.Sequential(
            nn.Linear(N_features, 512),
            nn.ReLU(),
            nn.Linear(512, N_labels),
        )
        
        self.accuracy = Accuracy()
        self.confusion = ConfusionMatrix(N_labels)
        self.weights = weights

    def forward(self, x):
        x = self.flatten(x)
        logits = self.linear_relu_stack(x)
        return logits

    def configure_optimizers(self):
        optimizer = torch.optim.SGD(
            self.parameters(), 
            lr=self.lr, 
            momentum=self.momentum,
            weight_decay=self.weight_decay
            
        )
        return optimizer

    def training_step(self, batch, batch_idx):
        x, y = batch
        y_hat = self(x)
        loss = F.cross_entropy(y_hat, y, weight=self.weights)
        acc = self.accuracy(y_hat.softmax(dim=-1), y)
        matrix = self.confusion(y_hat.softmax(dim=-1), y)
        
        self.log("train_loss", loss, on_step=False, on_epoch=True, logger=True)
        self.log("train_accuracy", acc, on_step=False, on_epoch=True, logger=True)
        self.log("train_confusion_mat", matrix, on_step=False, on_epoch=True, logger=True)
        return loss
    
    def validation_step(self, batch, batch_idx):
        x, y = batch
        y_hat = self(x)
        val_loss = F.cross_entropy(y_hat, y, weight=self.weights)
        acc = self.accuracy(y_hat.softmax(dim=-1), y)
        matrix = self.confusion(y_hat.softmax(dim=-1), y)
        
        self.log("val_loss", val_loss, on_step=False, on_epoch=True, logger=True)
        self.log("val_accuracy", acc, on_step=False, on_epoch=True, logger=True)
        self.log("val_confusion_mat", matrix, on_step=False, on_epoch=True, logger=True)
        return val_loss
    
    def train_dataloader(self):
        return DataLoader(self.train_data, batch_size=8, num_workers=0)

    def val_dataloader(self):
        return DataLoader(self.test_data, batch_size=8, num_workers=0)


In [18]:
from sklearn.utils.class_weight import compute_class_weight

def class_weights(label_df):
    label_df = pd.read_csv(label_df)
    
    weights = compute_class_weight(
        class_weight='balanced', 
        classes=np.unique(label_df), 
        y=label_df.values.reshape(-1)
    )

    weights = torch.from_numpy(weights)
    return weights.float()

weights = class_weights('fixed_primary_labels_neighbors_50_components_50_clust_size_100.csv')

Now let's set up RayTune

In [19]:
class UploadCallback(pl.callbacks.Callback):
    def __init__(self, path, WIDTH, LAYERS) -> None:
        super().__init__()
        self.path = path 
        self.width = WIDTH
        self.layers = LAYERS

    def on_train_epoch_end(self, trainer, pl_module):
        epoch = trainer.current_epoch
        trainer.save_checkpoint(f'checkpoints/checkpoint-{epoch}-width-{self.width}-layers-{self.layers}.ckpt')
        print(os.listdir('checkpoints'))
        print ('Uploading file...')

uploadcallback = UploadCallback('checkpoints', 10, 10)

Now let's set up RayTune

In [20]:
from ray.tune.integration.pytorch_lightning import TuneReportCallback
import ray.tune as tune 

raytunecallback = TuneReportCallback(
    {
        "loss": "val_loss", 
        "mean_accuracy": "val_accuracy"
    },
    on="validation_end"
)

In [23]:
def train_with_tune(config, max_epochs):
    model = GeneClassifier(t.num_features(), t.num_labels(), weights, config)
    
    trainer = pl.Trainer(
        max_epochs=max_epochs, 
        callbacks=[
            raytunecallback,
            uploadcallback,
        ]
    )
    
    trainer.fit(model)
    
def model_search(num_samples=10, max_epochs=10):
    config = {
        "lr" : tune.loguniform(1e-4, 1e-1),
        "momentum" : tune.loguniform(0.1, 0.8),
        "weight_decay" : tune.uniform(1e-4, 1e-1)
    }

    scheduler = ASHAScheduler(
        max_t=max_epochs,
        grace_period=1,
        reduction_factor=2)

    reporter = CLIReporter(
        parameter_columns = ["lr", "momentum", "weight_decay"],
        metric_columns=["loss", "mean_accuracy", "training_iteration"])

    train_fn_with_parameters = tune.with_parameters(train_with_tune, max_epochs=max_epochs)
                                            
    resources_per_trial = {"cpu": 1}

    analysis = tune.run(train_fn_with_parameters,
        resources_per_trial=resources_per_trial,
        metric="loss",
        mode="min",
        config=config,
        num_samples=num_samples,
        scheduler=scheduler,
        progress_reporter=reporter,
        name="model_search"
    )

    print("Best hyperparameters found were: ", analysis.best_config)

model_search()

== Status ==
Current time: 2021-12-15 15:56:45 (running for 00:00:00.16)
Memory usage on this node: 14.7/16.0 GiB: ***LOW MEMORY*** less than 10% of the memory on this node is available for use. This can cause unexpected crashes. Consider reducing the memory used by your application or reducing the Ray object store size by setting `object_store_memory` when calling `ray.init`.
Using AsyncHyperBand: num_stopped=0
Bracket: Iter 8.000: None | Iter 4.000: None | Iter 2.000: None | Iter 1.000: None
Resources requested: 0/10 CPUs, 0/0 GPUs, 0.0/8.53 GiB heap, 0.0/4.26 GiB objects
Result logdir: /Users/julian/ray_results/model_search
Number of trials: 10/10 (10 PENDING)
+-----------------------------+----------+-------+-------------+------------+----------------+
| Trial name                  | status   | loc   |          lr |   momentum |   weight_decay |
|-----------------------------+----------+-------+-------------+------------+----------------|
| train_with_tune_a8cac_00000 | PENDING  | 

(ImplicitFunc pid=41022) GPU available: False, used: False
(ImplicitFunc pid=41022) TPU available: False, using: 0 TPU cores
(ImplicitFunc pid=41022) IPU available: False, using: 0 IPUs
(ImplicitFunc pid=41022) /Users/julian/miniconda3/envs/base-data-science/lib/python3.9/site-packages/pytorch_lightning/trainer/configuration_validator.py:271: LightningDeprecationWarning: The `on_keyboard_interrupt` callback hook was deprecated in v1.5 and will be removed in v1.7. Please use the `on_exception` callback hook instead.
(ImplicitFunc pid=41022)   rank_zero_deprecation(
(ImplicitFunc pid=41022) 
(ImplicitFunc pid=41022)   | Name              | Type            | Params
(ImplicitFunc pid=41022) ------------------------------------------------------
(ImplicitFunc pid=41022) 0 | flatten           | Flatten         | 0     
(ImplicitFunc pid=41022) 1 | linear_relu_stack | Sequential      | 10.3 K
(ImplicitFunc pid=41022) 2 | accuracy          | Accuracy        | 0     
(ImplicitFunc pid=41022) 3 

(ImplicitFunc pid=41017)   rank_zero_warn(
(ImplicitFunc pid=41017) 2021-12-15 15:56:48,815	ERROR function_runner.py:268 -- Runner Thread raised error.
(ImplicitFunc pid=41017) Traceback (most recent call last):
(ImplicitFunc pid=41017)   File "/Users/julian/miniconda3/envs/base-data-science/lib/python3.9/site-packages/ray/tune/function_runner.py", line 262, in run
(ImplicitFunc pid=41017)     self._entrypoint()
(ImplicitFunc pid=41017)   File "/Users/julian/miniconda3/envs/base-data-science/lib/python3.9/site-packages/ray/tune/function_runner.py", line 330, in entrypoint
(ImplicitFunc pid=41017)     return self._trainable_func(self.config, self._status_reporter,
(ImplicitFunc pid=41017)   File "/Users/julian/miniconda3/envs/base-data-science/lib/python3.9/site-packages/ray/util/tracing/tracing_helper.py", line 451, in _resume_span
(ImplicitFunc pid=41017)     return method(self, *_args, **_kwargs)
(ImplicitFunc pid=41017)   File "/Users/julian/miniconda3/envs/base-data-science/lib/pyt

(ImplicitFunc pid=41022)   File "/Users/julian/miniconda3/envs/base-data-science/lib/python3.9/site-packages/pytorch_lightning/loops/dataloader/evaluation_loop.py", line 139, in on_run_end
(ImplicitFunc pid=41022)     self._on_evaluation_end()
(ImplicitFunc pid=41022)   File "/Users/julian/miniconda3/envs/base-data-science/lib/python3.9/site-packages/pytorch_lightning/loops/dataloader/evaluation_loop.py", line 201, in _on_evaluation_end
(ImplicitFunc pid=41022)     self.trainer.call_hook("on_validation_end", *args, **kwargs)
(ImplicitFunc pid=41022)   File "/Users/julian/miniconda3/envs/base-data-science/lib/python3.9/site-packages/pytorch_lightning/trainer/trainer.py", line 1490, in call_hook
(ImplicitFunc pid=41022)     callback_fx(*args, **kwargs)
(ImplicitFunc pid=41022)   File "/Users/julian/miniconda3/envs/base-data-science/lib/python3.9/site-packages/pytorch_lightning/trainer/callback_hook.py", line 221, in on_validation_end
(ImplicitFunc pid=41022)     callback.on_validation_en

2021-12-15 15:56:48,994	ERROR trial_runner.py:958 -- Trial train_with_tune_a8cac_00007: Error processing event.
Traceback (most recent call last):
  File "/Users/julian/miniconda3/envs/base-data-science/lib/python3.9/site-packages/ray/tune/trial_runner.py", line 924, in _process_trial
    results = self.trial_executor.fetch_result(trial)
  File "/Users/julian/miniconda3/envs/base-data-science/lib/python3.9/site-packages/ray/tune/ray_trial_executor.py", line 787, in fetch_result
    result = ray.get(trial_future[0], timeout=DEFAULT_GET_TIMEOUT)
  File "/Users/julian/miniconda3/envs/base-data-science/lib/python3.9/site-packages/ray/_private/client_mode_hook.py", line 105, in wrapper
    return func(*args, **kwargs)
  File "/Users/julian/miniconda3/envs/base-data-science/lib/python3.9/site-packages/ray/worker.py", line 1713, in get
    raise value.as_instanceof_cause()
ray.exceptions.RayTaskError(TuneError): ray::ImplicitFunc.train_buffered() (pid=41015, ip=127.0.0.1, repr=<ray.tune.funct

...

Validation sanity check:   0%|          | 0/2 [00:00<?, ?it/s]
Result for train_with_tune_a8cac_00005:
  date: 2021-12-15_15-56-48
  experiment_id: 94a764d8ffb243a898bf9fc75e3f7052
  hostname: MacBook-Pro.local
  node_ip: 127.0.0.1
  pid: 41017
  timestamp: 1639612608
  trial_id: a8cac_00005
  
Result for train_with_tune_a8cac_00001:
  date: 2021-12-15_15-56-48
  experiment_id: 0efdc37ef89740b5911b10fb37582550
  hostname: MacBook-Pro.local
  node_ip: 127.0.0.1
  pid: 41018
  timestamp: 1639612608
  trial_id: a8cac_00001
  
Result for train_with_tune_a8cac_00007:
  date: 2021-12-15_15-56-48
  experiment_id: 87bd45dca55b4f18b27568ac3d61edeb
  hostname: MacBook-Pro.local
  node_ip: 127.0.0.1
  pid: 41015
  timestamp: 1639612608
  trial_id: a8cac_00007
  
Result for train_with_tune_a8cac_00003:
  date: 2021-12-15_15-56-48
  experiment_id: ed95a8f3a8a14df8b2eb6364bc896195
  hostname: MacBook-Pro.local
  node_ip: 127.0.0.1
  pid: 41022
  timestamp: 1639612608
  trial_id: a8cac_00003
  
Resul

2021-12-15 15:56:49,043	ERROR trial_runner.py:958 -- Trial train_with_tune_a8cac_00002: Error processing event.
Traceback (most recent call last):
  File "/Users/julian/miniconda3/envs/base-data-science/lib/python3.9/site-packages/ray/tune/trial_runner.py", line 924, in _process_trial
    results = self.trial_executor.fetch_result(trial)
  File "/Users/julian/miniconda3/envs/base-data-science/lib/python3.9/site-packages/ray/tune/ray_trial_executor.py", line 787, in fetch_result
    result = ray.get(trial_future[0], timeout=DEFAULT_GET_TIMEOUT)
  File "/Users/julian/miniconda3/envs/base-data-science/lib/python3.9/site-packages/ray/_private/client_mode_hook.py", line 105, in wrapper
    return func(*args, **kwargs)
  File "/Users/julian/miniconda3/envs/base-data-science/lib/python3.9/site-packages/ray/worker.py", line 1713, in get
    raise value.as_instanceof_cause()
ray.exceptions.RayTaskError(TuneError): ray::ImplicitFunc.train_buffered() (pid=41020, ip=127.0.0.1, repr=<ray.tune.funct

(ImplicitFunc pid=41022) /Users/julian/miniconda3/envs/base-data-science/lib/python3.9/multiprocessing/resource_tracker.py:216: UserWarning: resource_tracker: There appear to be 1 leaked semaphore objects to clean up at shutdown
(ImplicitFunc pid=41022)   warnings.warn('resource_tracker: There appear to be %d '
(ImplicitFunc pid=41016) /Users/julian/miniconda3/envs/base-data-science/lib/python3.9/multiprocessing/resource_tracker.py:216: UserWarning: resource_tracker: There appear to be 1 leaked semaphore objects to clean up at shutdown
(ImplicitFunc pid=41016)   warnings.warn('resource_tracker: There appear to be %d '
(ImplicitFunc pid=41018) /Users/julian/miniconda3/envs/base-data-science/lib/python3.9/multiprocessing/resource_tracker.py:216: UserWarning: resource_tracker: There appear to be 1 leaked semaphore objects to clean up at shutdown
(ImplicitFunc pid=41018)   warnings.warn('resource_tracker: There appear to be %d '
(ImplicitFunc pid=41014) /Users/julian/miniconda3/envs/base-d

Result for train_with_tune_a8cac_00002:
  date: 2021-12-15_15-56-48
  experiment_id: bbd8789f6724464d95bc856f64c3f828
  hostname: MacBook-Pro.local
  node_ip: 127.0.0.1
  pid: 41020
  timestamp: 1639612608
  trial_id: a8cac_00002
  
Result for train_with_tune_a8cac_00000:
  date: 2021-12-15_15-56-48
  experiment_id: 4ad9589641f84c6589b47615d88292b6
  hostname: MacBook-Pro.local
  node_ip: 127.0.0.1
  pid: 41019
  timestamp: 1639612608
  trial_id: a8cac_00000
  
== Status ==
Current time: 2021-12-15 15:56:49 (running for 00:00:03.43)
Memory usage on this node: 14.5/16.0 GiB: ***LOW MEMORY*** less than 10% of the memory on this node is available for use. This can cause unexpected crashes. Consider reducing the memory used by your application or reducing the Ray object store size by setting `object_store_memory` when calling `ray.init`.
Using AsyncHyperBand: num_stopped=0
Bracket: Iter 8.000: None | Iter 4.000: None | Iter 2.000: None | Iter 1.000: None
Resources requested: 0/10 CPUs, 0/0

TuneError: ('Trials did not complete', [train_with_tune_a8cac_00000, train_with_tune_a8cac_00001, train_with_tune_a8cac_00002, train_with_tune_a8cac_00003, train_with_tune_a8cac_00004, train_with_tune_a8cac_00005, train_with_tune_a8cac_00006, train_with_tune_a8cac_00007, train_with_tune_a8cac_00008, train_with_tune_a8cac_00009])

In [ ]:
t[0]

In [ ]:
t = torch.from_numpy(a)
l = torch.from_numpy(l)
t.softmax(dim=-1)

In [ ]:
t.softmax(dim=-1)